In [2]:
import pandas as pd
import tensorflow as tf
from tensorflow.keras import preprocessing
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Embedding, Dense, Dropout, Conv1D, GlobalMaxPool1D, concatenate
from sklearn.model_selection import train_test_split
import numpy as np
np.set_printoptions(threshold=np.inf, linewidth=np.inf)

In [7]:
gpus = tf.config.experimental.list_physical_devices('GPU')
if gpus:
    try:
        for gpu in gpus:
            tf.config.experimental.set_memory_growth(gpu, True)
    except RuntimeError as e:
        print(e)

# 데이터 읽어오기
train_file = "c:/2nd_project/Data/talk_data/영화주제 대화 말뭉치 라벨링.csv"
data = pd.read_csv(train_file, delimiter=',')
###################################################
data = df[df['label'] != 0]
###################################################
queries = data['text'].tolist()
intents = data['label'].tolist()

from Preprocess2 import Preprocess2
p = Preprocess2(word2index_dic='c:/2nd_project/Data/chatbot_dict_talk.bin', userdic='c:/2nd_project/Data/user_dic.txt')

# 단어 시퀀스 생성
sequences = []
for sentence in queries:
    sentence = str(sentence)
    pos = p.pos(sentence)
    keywords = p.get_keywords(pos, without_tag=True)
    seq = p.get_wordidx_sequence(keywords)
    sequences.append(seq)

average_word_count = np.mean([len(seq) for seq in sequences])
median_word_count = np.median([len(seq) for seq in sequences])
print('단어 개수 평균값 :', average_word_count)
print('단어 개수 중앙값 :', median_word_count)

# 단어 인덱스 시퀀스 벡터
# 단어 시퀀스 벡터 크기
from GlobalParams import MAX_SEQ_LEN

padded_seqs = preprocessing.sequence.pad_sequences(sequences, maxlen=MAX_SEQ_LEN, padding='post')

print(padded_seqs.shape)
print(len(intents))

# 학습용, 검증용, 테스트용 데이터셋 생성
# 학습셋:검증셋:테스트셋 = 7:2:1
ds = tf.data.Dataset.from_tensor_slices((padded_seqs, intents))
ds = ds.shuffle(len(queries))

단어 개수 평균값 : 5.845408280349357
단어 개수 중앙값 : 5.0
(74079, 15)
74079


In [5]:
print(ds)

<ShuffleDataset element_spec=(TensorSpec(shape=(15,), dtype=tf.int32, name=None), TensorSpec(shape=(), dtype=tf.int32, name=None))>


In [ ]:
X_train, X_temp, y_train, y_temp = train_test_split(padded_seqs, intents, test_size=0.3, random_state=123)
X_val, X_test, y_val, y_test = train_test_split(X_temp, y_temp, test_size=0.33, random_state=123)

In [3]:
print(len(X_train))
X_train

51855


array([[   59,   742,  2082,   587,    17,   222,     4,     0,     0,     0],
       [  356,    17,     0,     0,     0,     0,     0,     0,     0,     0],
       [  422,   455,     0,     0,     0,     0,     0,     0,     0,     0],
       [  503,  3182,    13,    27,   690,     4,     0,     0,     0,     0],
       [    7,   232,    96,    19,  2088,     0,     0,     0,     0,     0],
       [   71,    13,   409,    67,    58,    20,    21,     0,     0,     0],
       [   90,   905,   664,     2,   417,    45,     0,     0,     0,     0],
       [   50,    37,    39,    45,  4993,     7,     0,     0,     0,     0],
       [    9,   168,    97,   249,    13,   354,    47,   177,     0,     0],
       [  100,     2,   357,  1239,   978,    84,    20,     7,     0,     0],
       [   27,    99,   222,   398,    17,    57,     0,     0,     0,     0],
       [ 4688,    85,   269,   790,   639,    21,     0,     0,     0,     0],
       [    1,  8026,     4,    44,    28,    49,   

In [4]:
print(len(y_train))
y_train

51855


[0,
 6,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 6,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 6,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 6,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 6,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 6,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 3,
 0,


In [5]:
print(len(X_val))
X_val

14890


array([[    5,    35,  1320,   103,     4,    83,     0,     0,     0,     0],
       [  643,    39,    20,    28,     0,     0,     0,     0,     0,     0],
       [  188,   143,    63,  3102,    13,   412,     4,    44,    28,     0],
       [  105,    30,     7,     0,     0,     0,     0,     0,     0,     0],
       [  363,   266,  2189,    30,    39,   678,  4886,   116,    20,     0],
       [  168,    65,    77,     2,    71,    30,     2,    49,     0,     0],
       [ 1529,   377,   870,     0,     0,     0,     0,     0,     0,     0],
       [   59, 13537,   891,    13,   304,     0,     0,     0,     0,     0],
       [   34,  1206,  3523,   846, 10908, 10909,     0,     0,     0,     0],
       [  709,    41,     3,     0,     0,     0,     0,     0,     0,     0],
       [  749,     0,     0,     0,     0,     0,     0,     0,     0,     0],
       [ 3962,    54,   275,     4,     4,    64,   122,    94,  2073,   136],
       [  767,  1892,   109,    32,   178,     2,   

In [6]:
print(len(y_val))
y_val

14890


[0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 6,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 6,
 0,
 0,
 0,
 0,
 6,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 6,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 4,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 6,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 6,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 6,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 6,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,


In [7]:
print(len(X_test))
X_test

7334


array([[15019,     0,     0,     0,     0,     0,     0,     0,     0,     0],
       [ 4950,     9,   479,  2153,    64,   518,     0,     0,     0,     0],
       [    7,    13,  1461,  1499,   140,     4,     0,     0,     0,     0],
       [  233,  4217,     4,   269,    26,    97,    21,     0,     0,     0],
       [    7,     3,     2,  1162,   522,   364,  8859,  6715,     7,     0],
       [  358,   654,     2,    13,     2,  1491,     4,     0,     0,     0],
       [ 1364,   164,   660,    48,     0,     0,     0,     0,     0,     0],
       [  168,    65,     2,   177,    96,    21,     7,     0,     0,     0],
       [  140,  2027,    55,    73,   207,    85,     4,     0,     0,     0],
       [    9,   233,    14,    65,     1,     4,   198,     2,     7,     0],
       [  207,   914,  1970,    77,   800,    35,     0,     0,     0,     0],
       [   29,   344,   552,  4563,     3,     0,     0,     0,     0,     0],
       [  465,   134,   163, 11136,     0,     0,   

In [8]:
print(len(y_test))
y_test

7334


[6,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 6,
 0,
 0,
 6,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 6,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 6,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 6,
 0,
 0,
 0,
 1,
 0,
 0,
 2,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 6,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 6,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 6,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 6,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,


In [9]:
train_ds = tf.data.Dataset.from_tensor_slices((X_train, y_train)).batch(20)
val_ds = tf.data.Dataset.from_tensor_slices((X_val, y_val)).batch(20)
test_ds = tf.data.Dataset.from_tensor_slices((X_test, y_test)).batch(20)

In [12]:
print(train_ds)
print(val_ds)
print(test_ds)

<BatchDataset element_spec=(TensorSpec(shape=(None, 10), dtype=tf.int32, name=None), TensorSpec(shape=(None,), dtype=tf.int32, name=None))>
<BatchDataset element_spec=(TensorSpec(shape=(None, 10), dtype=tf.int32, name=None), TensorSpec(shape=(None,), dtype=tf.int32, name=None))>
<BatchDataset element_spec=(TensorSpec(shape=(None, 10), dtype=tf.int32, name=None), TensorSpec(shape=(None,), dtype=tf.int32, name=None))>


In [13]:
print(Input(shape=(MAX_SEQ_LEN,)))

KerasTensor(type_spec=TensorSpec(shape=(None, 10), dtype=tf.float32, name='input_1'), name='input_1', description="created by layer 'input_1'")


In [15]:
# 하이퍼 파라미터 설정
dropout_prob = 0.5
EMB_SIZE = 128
EPOCH = 5
VOCAB_SIZE = len(p.word_index) + 1  # 전체 단어 개수

# CNN 모델 정의
input_layer = Input(shape=(MAX_SEQ_LEN,))
embedding_layer = Embedding(VOCAB_SIZE, EMB_SIZE, input_length=MAX_SEQ_LEN)(input_layer)
dropout_emb = Dropout(rate=dropout_prob)(embedding_layer)

conv1 = Conv1D(
    filters=128,
    kernel_size=3,
    padding='valid',
    activation=tf.nn.relu)(dropout_emb)
pool1 = GlobalMaxPool1D()(conv1)

hidden = Dense(128, activation=tf.nn.relu)(pool1)
dropout_hidden = Dropout(rate=dropout_prob)(hidden)
logits = Dense(6, name='logits')(dropout_hidden)
predictions = Dense(6, activation=tf.nn.softmax)(logits)

# 모델 생성
model = Model(inputs=input_layer, outputs=predictions)
model.compile(optimizer='adam',
              loss='sparse_categorical_crossentropy',
              metrics=['accuracy'])

# 모델 학습
with tf.device('/GPU:0'):
    model.fit(train_ds, validation_data=val_ds, epochs=EPOCH, verbose=1)

# 모델 평가(테스트 데이터 셋 이용)
with tf.device('/GPU:0'):
    loss, accuracy = model.evaluate(test_ds, verbose=1)
    print('Accuracy: %f' % (accuracy * 100))
    print('loss: %f' % (loss))

# 모델 저장
model.save('c:/2nd_project/Model/intent_model_0808_a.h5')

print('완료되었습니다.')

Epoch 1/5
2593/2593 [==============================] - 21s 8ms/step - loss: nan - accuracy: 0.9620 - val_loss: nan - val_accuracy: 0.9620
Epoch 2/5
2593/2593 [==============================] - 20s 8ms/step - loss: nan - accuracy: 0.9624 - val_loss: nan - val_accuracy: 0.9620
Epoch 3/5
2593/2593 [==============================] - 20s 8ms/step - loss: nan - accuracy: 0.9624 - val_loss: nan - val_accuracy: 0.9620
Epoch 4/5
2593/2593 [==============================] - 20s 8ms/step - loss: nan - accuracy: 0.9624 - val_loss: nan - val_accuracy: 0.9620
Epoch 5/5
367/367 [==============================] - 1s 3ms/step - loss: nan - accuracy: 0.9611
Accuracy: 96.113992
loss: nan
완료되었습니다.


In [ ]:
# 하이퍼 파라미터 설정
dropout_prob = 0.5
EMB_SIZE = 128
EPOCH = 5
VOCAB_SIZE = len(p.word_index) + 1  # 전체 단어 개수

# CNN 모델 정의
input_layer = Input(shape=(MAX_SEQ_LEN,))
embedding_layer = Embedding(VOCAB_SIZE, EMB_SIZE, input_length=MAX_SEQ_LEN)(input_layer)
dropout_emb = Dropout(rate=dropout_prob)(embedding_layer)
conv1 = Conv1D(
    filters=128,
    kernel_size=3,
    padding='valid',
    activation=tf.nn.relu)(dropout_emb)
pool1 = GlobalMaxPool1D()(conv1)

conv2 = Conv1D(
    filters=128,
    kernel_size=4,
    padding='valid',
    activation=tf.nn.relu)(dropout_emb)
pool2 = GlobalMaxPool1D()(conv2)

conv3 = Conv1D(
    filters=128,
    kernel_size=5,
    padding='valid',
    activation=tf.nn.relu)(dropout_emb)
pool3 = GlobalMaxPool1D()(conv3)

# 3,4,5gram 이후 합치기
concat = concatenate([pool1, pool2, pool3])
hidden = Dense(128, activation=tf.nn.relu)(concat)
dropout_hidden = Dropout(rate=dropout_prob)(hidden)
logits = Dense(6, name='logits')(dropout_hidden)
predictions = Dense(6, activation=tf.nn.softmax)(logits)

# 모델 생성
model = Model(inputs=input_layer, outputs=predictions)
model.compile(optimizer='adam',
              loss='sparse_categorical_crossentropy',
              metrics=['accuracy'])

# 모델 학습
with tf.device('/GPU:0'):
    model.fit(train_ds, validation_data=val_ds, epochs=EPOCH, verbose=1)

# 모델 평가(테스트 데이터 셋 이용)
with tf.device('/GPU:0'):
    loss, accuracy = model.evaluate(test_ds, verbose=1)
    print('Accuracy: %f' % (accuracy * 100))
    print('loss: %f' % (loss))

# 모델 저장
model.save('c:/2nd_project/Model/intent_model_0808_a.h5')

print('완료되었습니다.')